In [1]:
from google.colab import files
uploaded= files.upload()


Saving creditcard.csv.zip to creditcard.csv.zip


In [8]:
!pip install catboost

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.2/99.2 MB 9.8 MB/s eta 0:00:00


In [9]:
import pandas as pd

# Load data
df = pd.read_csv("creditcard.csv.zip")

print(df.shape)
df.head()


(284807, 31)


Time        V1        V2        V3        V4        V5        V6        V7  \
0   0.0 -1.359807 -0.072781  2.536347  1.378155 -0.338321  0.462388  0.239599   
1   0.0  1.191857  0.266151  0.166480  0.448154  0.060018 -0.082361 -0.078803   
2   1.0 -1.358354 -1.340163  1.773209  0.379780 -0.503198  1.800499  0.791461   
3   1.0 -0.966272 -0.185226  1.792993 -0.863291 -0.010309  1.247203  0.237609   
4   2.0 -1.158233  0.877737  1.548718  0.403034 -0.407193  0.095921  0.592941   

         V8        V9  ...       V21       V22       V23       V24       V25  \
0  0.098698  0.363787  ... -0.018307  0.277838 -0.110474  0.066928  0.128539   
1  0.085102 -0.255425  ... -0.225775 -0.638672  0.101288 -0.339846  0.167170   
2  0.247676 -1.514654  ...  0.247998  0.771679  0.909412 -0.689281 -0.327642   
3  0.377436 -1.387024  ... -0.108300  0.005274 -0.190321 -1.175575  0.647376   
4 -0.270533  0.817739  ... -0.009431  0.798278 -0.137458  0.141267 -0.206010   

        V26       V27       V28  Amount  Class  
0 -0.189115  0.133558 -0.021053  149.62      0  
1  0.125895 -0.008983  0.014724    2.69      0  
2 -0.139097 -0.055353 -0.059752  378.66      0  
3 -0.221929  0.062723  0.061458  123.50      0  
4  0.502292  0.219422  0.215153   69.99      0  

[5 rows x 31 columns]

In [10]:
print(df['Class'].value_counts())

# 0 = normal, 1 = fraud


Class
0    284315
1       492
Name: count, dtype: int64


In [14]:
from sklearn.model_selection import train_test_split

X = df.drop(['Class'], axis=1)
y = df['Class']

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42, stratify=y
)

print("Train samples:", len(y_train))
print("Test samples:", len(y_test))



Train samples: 227845
Test samples: 56962


In [12]:
from catboost import CatBoostClassifier
from sklearn.metrics import roc_auc_score

# Initialize model
model = CatBoostClassifier(
    iterations=1000,
    learning_rate=0.05,
    depth=6,
    scale_pos_weight=100,   # Handles heavy imbalance
    eval_metric='AUC',
    random_seed=42,
    verbose=100
)

# Train
model.fit(X_train, y_train, eval_set=(X_test, y_test), early_stopping_rounds=50)

# Predict fraud probability (anomaly score)
y_pred_proba = model.predict_proba(X_test)[:, 1]

auc = roc_auc_score(y_test, y_pred_proba)
print("ROC AUC Score:", auc)


0:	test: 0.9697521	best: 0.9697521 (0)	total: 134ms	remaining: 2m 14s
Stopped by overfitting detector  (50 iterations wait)

bestTest = 0.9811702537
bestIteration = 26

Shrink model to first 27 iterations.
ROC AUC Score: 0.9811702536951753


In [13]:
from sklearn.metrics import classification_report

threshold = 0.5
y_pred = (y_pred_proba > threshold).astype(int)

print(classification_report(y_test, y_pred))


              precision    recall  f1-score   support

           0       1.00      1.00      1.00     56864
           1       0.60      0.89      0.72        98

    accuracy                           1.00     56962
   macro avg       0.80      0.94      0.86     56962
weighted avg       1.00      1.00      1.00     56962

